# How to open/load the GloGEM per-glacier files

there are 1520 files in `netcdf_output_dyn_glogemflow` and 1520 files in `netcdf_output_dyn_glogem`. You can either download them individually or download the .zip files within the two folders. 

- In `netcdf_output_dyn_glogem`, all (or almost all glaciers are simulated) using a simplified model version (GloGEM)
- In `netcdf_output_dyn_glogemflow`, only those glaciers above 1km² that were run dynamically with GloGEMFlow are included

**Attention**:
- To get aggregated GloGEMflow estimates, you have to use all simulations from `netcdf_output_dyn_glogemflow`, and then in addition select all glacers within `netcdf_output_dyn_glogem` that were not yet simulated in  `netcdf_output_dyn_glogemflow`. An example workflow is shown below. 
- simulation_year =1 corresponds to simulation_year 0 in other experiments: make sure to shift the values if you are interested at a specifc time period (and not just in steady states)
- there are some files named "psl_cm6a-lr", but they should actually be "ipsl_cm6a-lr". 

In [10]:
import xarray as xr
import numpy as np

### GloGEMflow files

In [2]:
### these are just the ones above 1km2 (that were run via GloGEMflow)
path = '/home/www/lschuster/gmip3_glogem_flow_per_glacier_data/netcdf_output_dyn_glogemflow/netcdf_output_dyn/'
testfile = 'VanTricht_rgi11_dyn_1851-1870_mri-esm2-0_hist.nc'
ds_gf = xr.open_dataset(path+testfile)

In [18]:
ds_gf.volume_m3.max()

<xarray.DataArray 'volume_m3' ()> Size: 8B
array(1.39689564e+10)

In [3]:
ds_gf#.area_m2#.sel(simulation_year=1)

<xarray.Dataset> Size: 17MB
Dimensions:          (simulation_year: 5000, rgi_id: 216)
Coordinates:
  * simulation_year  (simulation_year) float64 40kB 1.0 2.0 ... 4.999e+03 5e+03
  * rgi_id           (rgi_id) <U14 12kB 'RGI60-11.00047' ... 'RGI60-11.03760'
Data variables:
    area_m2          (simulation_year, rgi_id) float64 9MB ...
    volume_m3        (simulation_year, rgi_id) float64 9MB ...
Attributes:
    contributor:       VanTricht
    contributor_mail:  vantricht@vaw.baug.ethz.ch
    creation_date:     26-Apr-2024 15:37:01
    reg_region:        rgi11
    period:            1851-1870
    gcm:               mri-esm2-0
    ssp:               hist
    information:       no info

In [4]:
ds_gf.rgi_id

<xarray.DataArray 'rgi_id' (rgi_id: 216)> Size: 12kB
array(['RGI60-11.00047', 'RGI60-11.00054', 'RGI60-11.00067', ...,
       'RGI60-11.03701', 'RGI60-11.03740', 'RGI60-11.03760'], dtype='<U14')
Coordinates:
  * rgi_id   (rgi_id) <U14 12kB 'RGI60-11.00047' ... 'RGI60-11.03760'

#### GloGEM files

In [5]:
path_2 = '/home/www/lschuster/gmip3_glogem_flow_per_glacier_data/netcdf_output_dyn_glogem/netcdf_output_dyn/'
testfile_2 = 'VanTricht_rgi11_dyn_1851-1870_mri-esm2-0_hist.nc'
ds_g = xr.open_dataset(path_2+testfile_2)

In [6]:
ds_g.rgi_id

<xarray.DataArray 'rgi_id' (rgi_id: 3644)> Size: 204kB
array(['RGI60-11.00013', 'RGI60-11.00014', 'RGI60-11.00015', ...,
       'RGI60-11.03922', 'RGI60-11.03923', 'RGI60-11.03924'], dtype='<U14')
Coordinates:
  * rgi_id   (rgi_id) <U14 204kB 'RGI60-11.00013' ... 'RGI60-11.03924'

In [7]:
# most or even all glaciers that are in GloGEMflow are also in the GloGEM file ...
common_glaciers = list(set(ds_gf.rgi_id.values) & set(ds_g.rgi_id.values))
len(common_glaciers)

216

#### --> to get per-glacier files you should take all glaciers that exist from GloGEMflow, andthen takethose that do not exist in GloGEMflow from GLoGEM ... 

In [8]:
# drop those glaciers from the GLoGEM file that are available from GloGEMflow
ds_g_without_common_glaciers = ds_g.drop_sel(rgi_id= common_glaciers)

In [20]:
ds_combined_volume = xr.concat(
    [
        ds_g_without_common_glaciers.volume_m3.load(),
        ds_gf.volume_m3.load()
    ],
    dim="rgi_id", join='outer'
)


In [21]:
ds_combined_volume

<xarray.DataArray 'volume_m3' (simulation_year: 5000, rgi_id: 3644)> Size: 146MB
array([[1.11000000e+06, 2.87900000e+07, 1.59000000e+06, ...,
        1.14262751e+08, 1.11945292e+08, 7.54012036e+07],
       [1.10000000e+06, 2.85900000e+07, 1.58000000e+06, ...,
        1.13695921e+08, 1.09081411e+08, 7.37605543e+07],
       [1.10000000e+06, 2.84100000e+07, 1.58000000e+06, ...,
        1.12166925e+08, 1.04519736e+08, 7.05637441e+07],
       ...,
       [           nan,            nan,            nan, ...,
        5.24551296e+07, 5.34348286e+05, 1.38502444e+07],
       [           nan,            nan,            nan, ...,
        5.17504680e+07, 5.28105862e+05, 1.35843721e+07],
       [           nan,            nan,            nan, ...,
        5.07816183e+07, 5.29741761e+05, 1.37612858e+07]])
Coordinates:
  * simulation_year  (simulation_year) float64 40kB 1.0 2.0 ... 4.999e+03 5e+03
  * rgi_id           (rgi_id) <U14 204kB 'RGI60-11.00013' ... 'RGI60-11.03760'
Attributes:
    units:      m3
    long_name:  Glacier volume at timestam

**Check unit**